In [ ]:
%matplotlib inline


# Store observables


## Introduction
In this example,
we will learn how to store the history of state variables using the
:meth:`~gemseo.core.scenario.Scenario.add_observable` method.
This is useful in situations where we wish to access, post-process,
or save the values of discipline outputs that are not design variables,
constraints or objective functions.

## The Sellar problem
We will consider in this example the Sellar problem:

.. include:: /tutorials/_description/sellar_problem_definition.inc

## Imports
All the imports needed for the tutorials are performed here.



In [ ]:
from __future__ import annotations

from gemseo.algos.design_space import DesignSpace
from gemseo.api import configure_logger
from gemseo.api import create_discipline
from gemseo.api import create_scenario
from matplotlib import pyplot as plt
from numpy import array
from numpy import ones

configure_logger()

## Create the problem disciplines
In this section,
we use the available classes :class:`.Sellar1`, :class:`.Sellar2`
and :class:`.SellarSystem` to define the disciplines of the problem.
The :meth:`~gemseo.api.create_discipline` API function allows us to
carry out this task easily, as well as store the instances in a list
to be used later on.



In [ ]:
disciplines = create_discipline(["Sellar1", "Sellar2", "SellarSystem"])

## Create and execute the scenario

### Create the design space
In this section,
we define the design space which will be used for the creation of the MDOScenario.



In [ ]:
design_space = DesignSpace()
design_space.add_variable("x_local", 1, l_b=0.0, u_b=10.0, value=ones(1))
design_space.add_variable(
    "x_shared", 2, l_b=(-10, 0.0), u_b=(10.0, 10.0), value=array([4.0, 3.0])
)

### Create the scenario
In this section,
we build the MDO scenario which links the disciplines with the formulation,
the design space and the objective function.



In [ ]:
scenario = create_scenario(
    disciplines, formulation="MDF", objective_name="obj", design_space=design_space
)

### Add the constraints
Then,
we have to set the design constraints



In [ ]:
scenario.add_constraint("c_1", "ineq")
scenario.add_constraint("c_2", "ineq")

### Add the observables
Only the design variables, objective function and constraints are stored by
default. In order to be able to recover the data from the state variables,
y1 and y2, we have to add them as observables. All we have to do is enter
the variable name as a string to the
:meth:`~gemseo.core.scenario.Scenario.add_observable` method.
If more than one output name is provided (as a list of strings),
the observable function returns a concatenated array of the output values.



In [ ]:
scenario.add_observable("y_1")

It is also possible to add the observable with a custom name,
using the option `observable_name`. Let us store the variable `y_2` as `y2`.



In [ ]:
scenario.add_observable("y_2", observable_name="y2")

### Execute the scenario
Then,
we execute the MDO scenario with the inputs of the MDO scenario as a dictionary.
In this example,
the gradient-based `SLSQP` optimizer is selected, with 10 iterations at maximum:



In [ ]:
scenario.execute(input_data={"max_iter": 10, "algo": "SLSQP"})

## Access the observable variables
Retrieve observables from a dataset
^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^^
In order to create a dataset, we use the
corresponding :class:`.OptimizationProblem`:



In [ ]:
opt_problem = scenario.formulation.opt_problem

We can easily build a dataset from this :class:`.OptimizationProblem`:
either by separating the design parameters from the functions
(default option):



In [ ]:
dataset = opt_problem.export_to_dataset("sellar_problem")
print(dataset)

or by considering all features as default parameters:



In [ ]:
dataset = opt_problem.export_to_dataset("sellar_problem", categorize=False)
print(dataset)

or by using an input-output naming rather than an optimization naming:



In [ ]:
dataset = opt_problem.export_to_dataset("sellar_problem", opt_naming=False)
print(dataset)

#### Access observables by name
We can get the observable data by name,
either as a dictionary indexed by the observable names (default option):



In [ ]:
print(dataset.get_data_by_names(["y_1", "y2"]))

or as an array:



In [ ]:
print(dataset.get_data_by_names(["y_1", "y2"], False))

### Use the observables in a post-processing method
Finally,
we can generate plots with the observable variables. Have a look at the
Basic History plot and the Scatter Plot Matrix:



In [ ]:
scenario.post_process(
    "BasicHistory", variable_names=["obj", "y_1", "y2"], save=False, show=False
)
scenario.post_process(
    "ScatterPlotMatrix",
    save=False,
    show=False,
    variable_names=["obj", "c_1", "c_2", "y2", "y_1"],
)
# Workaround for HTML rendering, instead of ``show=True``
plt.show()